In [32]:
#Variables
p = 19 # Ha de ser un nombre primer
m = 1 # Un natural qualsevol
q = p^m
F = GF(q) # Cos finit de q elements
n = 6 # n és la longitud del codi, pot ser qualsevol natural menor o igual que q
k = 2 # k és la dimensió i ha de ser més petita que n
r = n - k # r és la redundància del codi
t = RR(r/2).floor() # capacitat correctora

In [33]:
#Definim un llistat de n alphas diferents del cos F
alphas = []
while len(alphas) < n:
    alpha = F.random_element()
    if not (alpha in alphas):
        alphas.append(alpha)
print alphas

[16, 9, 1, 10, 18, 4]


In [34]:
#Definim un llistat de n h's diferents de 0 del cos F
h = []
while len(h) < n:
    hi = F.random_element()
    if not (hi == 0):
        h.append(hi)
print h

[17, 6, 11, 13, 1, 14]


In [35]:
#Definim la matriu de control H dels codis Alternants
H = Matrix(F,r,n,0)
for i in range(r):
    for j in range(n):
        H[i,j] = h[j]*alphas[j]^i
print H

[17  6 11 13  1 14]
[ 6 16 11 16 18 18]
[ 1 11 11  8  1 15]
[16  4 11  4 18  3]


In [36]:
# Trobem la matriu generadora G sabent que GH^T=0
G = H.transpose().left_kernel().matrix()

In [37]:
 #Ara, podem codificar qualsevol paraula de F^k
u = [F.random_element() for i in range(k)] # Missatge
m_matrix = Matrix(F,1,k,u) # Missatge vist com a matriu d'una fila
print 'Vull enviar el missatge', u

Vull enviar el missatge [1, 17]


In [38]:
#Codifiquem el missatge fent uG
x = m_matrix*G #codifiquem el missatge
print 'El missatge codificat és', x

El missatge codificat és [ 1 17  1 16  2 11]


In [39]:
#Creem errors aleatoris per introduir al missatge
posicions_error = [] # Ens determina en quines coordenades hi haurà error
errors = []
while len(posicions_error) < t: #El codi pot corregir com a molt t errors, aleshores haurem de canviar t coordenades
    index = ZZ.random_element(0,n)
    if not index in posicions_error:
        posicions_error.append(index)
    while len(errors) < t:
        a = F.random_element()
        if not (a == x[0,index]):
            errors.append(a)
print 'posicions error = ', posicions_error
print 'errors = ', errors

posicions error =  [3, 5]
errors =  [15, 15]


In [40]:
# Introduim els errors al missatge rebut x. El missatge amb errors serà y
y = vector(F,n)
for i in range(n):
    y[i] = x[0,i] #Primer definim y igual a x i li apliquem els errors
for i in range(t):
    y[posicions_error[i]] = errors[i]
print 'El missatge amb errors és:', y

El missatge amb errors és: (1, 17, 1, 15, 2, 15)


In [41]:
# Definim el vector síndrome que és yH^T
s = y*H.transpose()
print s

(5, 18, 14, 8)


In [42]:
# Definim l'anell de polinomis amb coeficients a F i variable z
R.<z> = PolynomialRing(F)

In [49]:
# Definim el polinomi síndrome S(z)
S = s[0]*z^0
for i in range(1,r):
    S = S + s[i]*z^i
print S

8*z^3 + 14*z^2 + 18*z + 5


In [50]:
# Algoritme de Sugiyama
res_0 = z^r
res_1 = S
v_0 = 0
v_1 = 1
while (res_1).degree() >= t:
    quo = res_0 // res_1
    res = res_0 - quo*res_1
    v = v_0 - quo*v_1
    res_0 = res_1
    res_1 = res
    v_0 = v_1
    v_1 = v
print v_1
print res_1

10*z^2 + 6*z + 5
6*z + 6


In [51]:
# A partir de v i res, podem definir epsilon i sigma
epsilon = res_1
sigma = v_1
# A més, sabem que les arrels del polinomi localitzador d'errors ens dóna les inverses dels localitzadors
arrels = sigma.roots() # Ens dóna una llista de llistes. Cada solució té la seva multiplicitat.
loc_errors = vector (F,len(arrels))
coord = vector (ZZ,len(arrels))
for i in range(len(arrels)):
    loc_errors[i] = 1/(arrels[i][0])
print loc_errors
# Les coordenades d'errors són les m tal que loc_errors=alpha_m
t = 0
for i in range(n): # Recorre alpha
    for j in range(len(arrels)): #Recorre loc_errors
        if loc_errors[j] == alphas[i]:
            coord[t] = i
            t = t+1
print 'Els errors estan a les coordenades:', coord

(4, 10)
Els errors estan a les coordenades: (3, 5)


In [64]:
# Ara derivem sigma per fer-la servir a la formula de Forney
dsigma = sigma.diff()
# Apliquem Forney per trobar els errors
e = vector(F, n)# Vector d'errors inicialitzat a 0
for i in range(len(arrels)):
    num = loc_errors[i]*epsilon(arrels[i][0])
    denom = h[coord[i]]*dsigma(arrels[i][0])
    e[coord[i]] = -num/denom
print e
# Com que y = x + e, aleshores, x = y - e
m_corregit = vector(F,n)
m_corregit = y - e
print 'El missatge corregit és:', m_corregit
# Comprovació. Ha de ser tot zeros.
for i in range(n):
    m_corregit[i] = m_corregit[i] - x[0,i]

(0, 0, 0, 16, 0, 14)
El missatge corregit és: (1, 17, 1, 18, 2, 1)
